# **Começar pela Fase 1: Análise de Dados Intrínsecos (ADI)**
 É a abordagem mais lógica e fundamental. Antes de compararmos com o mundo exterior, precisamos ter certeza de que entendemos o comportamento individual de cada sensor: quão estáveis, confiáveis e "limpos" são os dados que eles produzem.

Para colocar essa fase em prática, preparei um novo script que se integra perfeitamente ao nosso pipeline anterior. Ele adiciona três novas sub-rotinas de análise, cada uma focada em um aspecto da confiabilidade e precisão, e apresenta os resultados de forma visual e interativa.

**<u>Este script irá</u>**:

1. **Analisar a Estabilidade**: Calcular e plotar o desvio padrão de cada sensor para ranquear os mais estáveis.

2. **Analisar Ruído e Outliers**: Criar boxplots para visualizar a distribuição dos dados e identificar sensores com leituras anômalas.

3. **Analisar a Disponibilidade**: Calcular a porcentagem de dados ausentes para cada sensor, medindo sua confiabilidade operacional.

In [ ]:
# V.1 - Agora com a inclusão do período de coletas de dados de todos os sensores e que estão no banco de dados do Influx.

# 0. PRÉ-CONFIGURAÇÕES | INSTALAÇÃO DE DEPENDÊNCIAS
import subprocess
import sys

def instalar_biblioteca(nome_biblioteca):
    """Instala uma biblioteca usando pip de forma silenciosa."""
    subprocess.check_call([sys.executable, "-m", "pip", "install", "--quiet", nome_biblioteca])

def verificar_bibliotecas():
    """Verifica se as bibliotecas necessárias estão instaladas e as instala se necessário."""
    bibliotecas = ['influxdb_client', 'openpyxl', 'plotly']
    print("--- Verificando dependências ---")
    for biblioteca in bibliotecas:
        try:
            __import__(biblioteca)
            print(f"Biblioteca '{biblioteca}' encontrada.")
        except ImportError:
            print(f"Biblioteca '{biblioteca}' não encontrada. Tentando instalar...")
            instalar_biblioteca(biblioteca)
    print("---------------------------------")

verificar_bibliotecas()

import pandas as pd
import influxdb_client
import plotly.express as px
import plotly.graph_objects as go

# 1. CONFIGURAÇÕES INICIAIS ---
influx_url = "https://tsdb.feira-de-jogos.dev.br"
influx_token = "Copiar e colar a key-api do influxDB aqui" #Removi minha chave Germano, tens que colocar a tua.
influx_org = "feira"
influx_bucket = "feira"

pd.set_option('display.max_columns', None)
pd.set_option('display.width', 1000)  # modifica à vontade para exibir quantas linhas achar necessário. Eu exagerei.
pd.set_option('display.max_rows', 100) # aqu também

# FUNÇÕES DE PROCESSAMENTO E ANÁLISE

def limpar_dados(df_bruto):
    """Realiza a limpeza do DataFrame bruto, separando registros válidos e inválidos."""
    print("\n--- Sub-rotina: Limpeza de Dados ---")
    df = df_bruto.copy()
    colunas_sensores = [col for col in df.columns if col.startswith('temp.')]
    indices_invalidos = df[colunas_sensores].isnull().any(axis=1)
    df_invalidos = df[indices_invalidos]
    df_limpo = df.dropna(subset=colunas_sensores)
    print(f"Registros válidos: {len(df_limpo)} | Registros com dados ausentes: {len(df_invalidos)}")
    return df_limpo, df_invalidos
## Não ficou automatizada ... necessário mudar a janela de forma manual ... para 3 min, 5 min ...
def agregar_dados_por_janela(df_para_agregar, janela='2min'):
    """Realiza o tratamento e a agregação dos dados limpos."""
    print(f"\n--- Sub-rotina: Agregação de Dados (Janelas de {janela}) ---")
    df = df_para_agregar.set_index('_time')
    colunas_sensores = [col for col in df.columns if col.startswith('temp.')]
    df_agregado = df[colunas_sensores].resample(janela).agg(['mean', 'std'])
    return df_agregado

def exibir_intervalo_de_dados(df_bruto):
    """
    Calcula e exibe o intervalo de tempo real (primeiro e último timestamp) dos dados coletados.
    """
    print("\n--- ANÁLISE 0: PERÍODO REAL DOS DADOS COLETADOS ---")
    if '_time' in df_bruto.columns and not df_bruto.empty:
        data_inicio = df_bruto['_time'].min()
        data_fim = df_bruto['_time'].max()
        print("O intervalo de dados a ser solicitado para as estações oficiais é:")
        print(f"  - Data de Início: {data_inicio.strftime('%d de %B de %Y, %H:%M:%S')}")
        print(f"  - Data de Fim:    {data_fim.strftime('%d de %B de %Y, %H:%M:%S')}")
    else:
        print("Não foi possível determinar o intervalo de datas (DataFrame vazio ou sem coluna '_time').")

def analisar_estabilidade(df_agregado):
    """
    Analisa a estabilidade (precisão) dos sensores com base no desvio padrão.
    """
    print("\n--- ANÁLISE 1.1: ESTABILIDADE (DESVIO PADRÃO) ---")
    df_std = df_agregado.xs('std', level=1, axis=1)
    df_std.columns = [col.replace('temp.', '') for col in df_std.columns]
    std_medio = df_std.mean().sort_values()
    print("\nRanking de Estabilidade (menor desvio padrão médio é melhor):")
    display(std_medio.to_frame(name='Desvio Padrão Médio (°C)'))
    fig = px.bar(std_medio, orientation='h',
                 labels={'value': 'Desvio Padrão Médio (°C)', 'index': 'Sensor'},
                 title='Ranking de Estabilidade dos Sensores',
                 text_auto='.4f')
    fig.update_layout(showlegend=False, title_x=0.5)
    fig.show()

def analisar_outliers(df_agregado):
    """
    Analisa a distribuição dos dados e a presença de outliers usando boxplots.
    """
    print("\n--- ANÁLISE 1.2: RUÍDO E OUTLIERS ---")
    df_media = df_agregado.xs('mean', level=1, axis=1)
    df_media.columns = [col.replace('temp.', '') for col in df_media.columns]
    df_melted = df_media.melt(var_name='Sensor', value_name='Temperatura Média (°C)')
    fig = px.box(df_melted, x='Sensor', y='Temperatura Média (°C)',
                 title='Distribuição das Leituras de Temperatura e Outliers por Sensor')
    fig.update_layout(title_x=0.5)
    fig.show()

def analisar_disponibilidade(df_bruto):
    """
    Analisa a confiabilidade operacional dos sensores calculando a porcentagem de dados ausentes.
    """
    print("\n--- ANÁLISE 1.3: DISPONIBILIDADE DE DADOS (CONFIABILIDADE) ---")
    colunas_sensores = [col for col in df_bruto.columns if col.startswith('temp.')]
    df_sensores = df_bruto[colunas_sensores]
    taxa_falha = (df_sensores.isnull().sum() / len(df_sensores)) * 100
    taxa_falha = taxa_falha.sort_values(ascending=False)
    print("\nTaxa de Falha (percentual de dados ausentes por sensor):")
    display(taxa_falha.to_frame(name='Taxa de Falha (%)'))
    fig = px.bar(taxa_falha,
                 labels={'value': 'Taxa de Falha (%)', 'index': 'Sensor'},
                 title='Ranking de Confiabilidade (Menor Taxa de Falha é Melhor)',
                 text_auto='.2f')
    fig.update_layout(showlegend=False, title_x=0.5)
    fig.show()


# BLOCO DE EXECUÇÃO PRINCIPAL

# 2. Conexão e Extração (aqui o milagre é o santo grau para raspar os dados do influx ...)
client = influxdb_client.InfluxDBClient(url=influx_url, token=influx_token, org=influx_org)
query_api = client.query_api()
flux_query = f'''
import "strings"
from(bucket: "{influx_bucket}")
  |> range(start: -45d)
  |> filter(fn: (r) => r["v"] == "1")
  |> filter(fn: (r) => strings.hasPrefix(v: r["_field"], prefix: "temp."))
  |> pivot(rowKey:["_time"], columnKey: ["_field"], valueColumn: "_value")
'''
print("\nBuscando dados de temperatura da Estação V1...")
df_temperatura_v1 = pd.DataFrame()
try:
    df_temperatura_v1 = query_api.query_data_frame(query=flux_query, org=influx_org)

    if not df_temperatura_v1.empty:
        print(f"Sucesso! Foram encontrados {len(df_temperatura_v1)} registros brutos.")

        # 3. ANÁLISE PRELIMINAR E PROCESSAMENTO
        exibir_intervalo_de_dados(df_temperatura_v1)
        df_limpo, df_invalidos = limpar_dados(df_temperatura_v1)
        df_agregado = agregar_dados_por_janela(df_limpo, janela='2min')

        # 4. FASE 1: ANÁLISE DE DADOS INTRÍNSECOS
        analisar_estabilidade(df_agregado)
        analisar_outliers(df_agregado)
        analisar_disponibilidade(df_temperatura_v1)

    else:
        print("Nenhum dado encontrado para os filtros especificados.")

except Exception as e:
    print(f"Ocorreu um erro durante a extração: {e}")

finally:
  client.close()

--- Verificando dependências ---
Biblioteca 'influxdb_client' encontrada.
Biblioteca 'openpyxl' encontrada.
Biblioteca 'plotly' encontrada.
---------------------------------

Buscando dados de temperatura da Estação V1...
Sucesso! Foram encontrados 28133 registros brutos.

--- ANÁLISE 0: PERÍODO REAL DOS DADOS COLETADOS ---
O intervalo de dados a ser solicitado para as estações oficiais é:
  - Data de Início: 19 de August de 2025, 17:58:35
  - Data de Fim:    01 de September de 2025, 11:39:04

--- Sub-rotina: Limpeza de Dados ---
Registros válidos: 25310 | Registros com dados ausentes: 2823

--- Sub-rotina: Agregação de Dados (Janelas de 2min) ---

--- ANÁLISE 1.1: ESTABILIDADE (DESVIO PADRÃO) ---

Ranking de Estabilidade (menor desvio padrão médio é melhor):


Desvio Padrão Médio (°C)
bmp280                   0.005781
bmp388                   0.005924
bmp180                   0.005987
bme280                   0.006245
dht11                    0.007576
lm35dz                   0.008584
aht10                    0.012737
dht22                    0.013257
aht25                    0.014026
mcp9808                  0.021602
ds18b20                  0.021616
lm75                     0.067322


--- ANÁLISE 1.2: RUÍDO E OUTLIERS ---



--- ANÁLISE 1.3: DISPONIBILIDADE DE DADOS (CONFIABILIDADE) ---

Taxa de Falha (percentual de dados ausentes por sensor):


Taxa de Falha (%)
temp.aht25            10.034479
temp.aht10             0.000000
temp.bme280            0.000000
temp.bmp180            0.000000
temp.bmp280            0.000000
temp.bmp388            0.000000
temp.dht11             0.000000
temp.dht22             0.000000
temp.ds18b20           0.000000
temp.lm35dz            0.000000
temp.lm75              0.000000
temp.mcp9808           0.000000

In [ ]:
# 0. PRÉ-CONFIGURAÇÕES | INSTALAÇÃO DE DEPENDÊNCIAS
import subprocess
import sys

def instalar_biblioteca(nome_biblioteca):
    """Instala uma biblioteca usando pip de forma silenciosa."""
    subprocess.check_call([sys.executable, "-m", "pip", "install", "--quiet", nome_biblioteca])

def verificar_bibliotecas():
    """Verifica se as bibliotecas necessárias estão instaladas e as instala se necessário."""
    bibliotecas = ['influxdb_client', 'openpyxl', 'plotly']
    print("--- Verificando dependências ---")
    for biblioteca in bibliotecas:
        try:
            __import__(biblioteca)
            print(f"Biblioteca '{biblioteca}' encontrada.")
        except ImportError:
            print(f"Biblioteca '{biblioteca}' não encontrada. Tentando instalar...")
            instalar_biblioteca(biblioteca)
    print("---------------------------------")

verificar_bibliotecas()

import pandas as pd
import influxdb_client
import plotly.express as px
import plotly.graph_objects as go

# 1. CONFIGURAÇÕES INICIAIS
influx_url = "https://tsdb.feira-de-jogos.dev.br"
influx_token = "Key API do INFLUXDB"
influx_org = "feira"
influx_bucket = "feira"

pd.set_option('display.max_columns', None)
pd.set_option('display.width', 1000)
pd.set_option('display.max_rows', 100)

# FUNÇÕES DE PROCESSAMENTO E ANÁLISE

def solicitar_intervalo_usuario(df_bruto):
    """
    Solicita ao usuário as datas de início e fim para a análise e filtra o DataFrame.
    """
    print("\n--- DEFINIÇÃO DO PERÍODO DE ANÁLISE ---")
    if '_time' not in df_bruto.columns or df_bruto.empty:
        print("DataFrame vazio ou sem coluna '_time'. Não é possível solicitar intervalo.")
        return pd.DataFrame() # Retorna um DataFrame vazio

    data_inicio_disponivel = df_bruto['_time'].min()
    data_fim_disponivel = df_bruto['_time'].max()

    print(f"Dados disponíveis de {data_inicio_disponivel.strftime('%Y-%m-%d')} a {data_fim_disponivel.strftime('%Y-%m-%d')}.")

    try:
        data_inicio_str = input(f"Digite a data de início (formato AAAA-MM-DD): ")
        data_fim_str = input(f"Digite a data de fim (formato AAAA-MM-DD): ")

        # Converte as strings para datetimes com fuso horário UTC para comparação correta
        data_inicio = pd.to_datetime(data_inicio_str).tz_localize('UTC')
        # Adiciona o final do dia para garantir que todos os dados do dia final sejam incluídos
        data_fim = pd.to_datetime(data_fim_str + " 23:59:59").tz_localize('UTC')

        print(f"\nFiltrando dados de {data_inicio.date()} até {data_fim.date()}...")
        df_filtrado = df_bruto[(df_bruto['_time'] >= data_inicio) & (df_bruto['_time'] <= data_fim)].copy()

        if df_filtrado.empty:
            print("Nenhum registro encontrado no período selecionado.")
        else:
            print(f"Foram encontrados {len(df_filtrado)} registros no período selecionado.")

        return df_filtrado

    except (ValueError, TypeError):
        print("Formato de data inválido ou entrada incorreta. Use AAAA-MM-DD. Análise abortada.")
        return pd.DataFrame() # Retorna DataFrame vazio em caso de erro

def limpar_dados(df_bruto):
    """Realiza a limpeza do DataFrame bruto, separando registros válidos e inválidos."""
    print("\n--- Sub-rotina: Limpeza de Dados ---")
    df = df_bruto.copy()
    colunas_sensores = [col for col in df.columns if col.startswith('temp.')]
    indices_invalidos = df[colunas_sensores].isnull().any(axis=1)
    df_invalidos = df[indices_invalidos]
    df_limpo = df.dropna(subset=colunas_sensores)
    print(f"Registros válidos: {len(df_limpo)} | Registros com dados ausentes: {len(df_invalidos)}")
    return df_limpo, df_invalidos

def agregar_dados_por_janela(df_para_agregar, janela='2min'):
    """Realiza o tratamento e a agregação dos dados limpos."""
    print(f"\n--- Sub-rotina: Agregação de Dados (Janelas de {janela}) ---")
    df = df_para_agregar.set_index('_time')
    colunas_sensores = [col for col in df.columns if col.startswith('temp.')]
    df_agregado = df[colunas_sensores].resample(janela).agg(['mean', 'std'])
    return df_agregado

def analisar_estabilidade(df_agregado):
    """
    Analisa a estabilidade (precisão) dos sensores com base no desvio padrão.
    """
    print("\n--- ANÁLISE 1.1: ESTABILIDADE (DESVIO PADRÃO) ---")
    df_std = df_agregado.xs('std', level=1, axis=1)
    df_std.columns = [col.replace('temp.', '') for col in df_std.columns]
    std_medio = df_std.mean().sort_values()
    print("\nRanking de Estabilidade (menor desvio padrão médio é melhor):")
    display(std_medio.to_frame(name='Desvio Padrão Médio (°C)'))
    fig = px.bar(std_medio, orientation='h',
                 labels={'value': 'Desvio Padrão Médio (°C)', 'index': 'Sensor'},
                 title='Ranking de Estabilidade dos Sensores',
                 text_auto='.4f')
    fig.update_layout(showlegend=False, title_x=0.5)
    fig.show()

def analisar_outliers(df_agregado):
    """
    Analisa a distribuição dos dados e a presença de outliers usando boxplots.
    """
    print("\n--- ANÁLISE 1.2: RUÍDO E OUTLIERS ---")
    df_media = df_agregado.xs('mean', level=1, axis=1)
    df_media.columns = [col.replace('temp.', '') for col in df_media.columns]
    df_melted = df_media.melt(var_name='Sensor', value_name='Temperatura Média (°C)')
    fig = px.box(df_melted, x='Sensor', y='Temperatura Média (°C)',
                 title='Distribuição das Leituras de Temperatura e Outliers por Sensor')
    fig.update_layout(title_x=0.5)
    fig.show()

def analisar_disponibilidade(df_bruto):
    """
    Analisa a confiabilidade operacional dos sensores calculando a porcentagem de dados ausentes.
    """
    print("\n--- ANÁLISE 1.3: DISPONIBILIDADE DE DADOS (CONFIABILIDADE) ---")
    colunas_sensores = [col for col in df_bruto.columns if col.startswith('temp.')]
    df_sensores = df_bruto[colunas_sensores]
    taxa_falha = (df_sensores.isnull().sum() / len(df_sensores)) * 100 if len(df_sensores) > 0 else 0
    taxa_falha = taxa_falha.sort_values(ascending=False)
    print("\nTaxa de Falha (percentual de dados ausentes por sensor):")
    display(taxa_falha.to_frame(name='Taxa de Falha (%)'))
    fig = px.bar(taxa_falha,
                 labels={'value': 'Taxa de Falha (%)', 'index': 'Sensor'},
                 title='Ranking de Confiabilidade (Menor Taxa de Falha é Melhor)',
                 text_auto='.2f')
    fig.update_layout(showlegend=False, title_x=0.5)
    fig.show()


# BLOCO DE EXECUÇÃO PRINCIPAL

# 2. Conexão e Extração
client = influxdb_client.InfluxDBClient(url=influx_url, token=influx_token, org=influx_org)
query_api = client.query_api()
flux_query = f'''
import "strings"
from(bucket: "{influx_bucket}")
  |> range(start: -45d)
  |> filter(fn: (r) => r["v"] == "1")
  |> filter(fn: (r) => strings.hasPrefix(v: r["_field"], prefix: "temp."))
  |> pivot(rowKey:["_time"], columnKey: ["_field"], valueColumn: "_value")
'''
print("\nBuscando dados de temperatura da Estação V1...")
df_total = pd.DataFrame()
try:
    df_total = query_api.query_data_frame(query=flux_query, org=influx_org)

    if not df_total.empty:
        print(f"Sucesso! Foram encontrados {len(df_total)} registros brutos no total.")

        # 3. FILTRAGEM INTERATIVA POR PERÍODO
        df_periodo_analise = solicitar_intervalo_usuario(df_total)

        # 4. ANÁLISE PRELIMINAR E PROCESSAMENTO (SOMENTE NO PERÍODO SELECIONADO)
        if not df_periodo_analise.empty:
            df_limpo, df_invalidos = limpar_dados(df_periodo_analise)
            df_agregado = agregar_dados_por_janela(df_limpo, janela='2min')

            # 5. FASE 1: ANÁLISE DE DADOS INTRÍNSECOS
            analisar_estabilidade(df_agregado)
            analisar_outliers(df_agregado)
            analisar_disponibilidade(df_periodo_analise)

    else:
        print("Nenhum dado encontrado para os filtros especificados na consulta inicial.")

except Exception as e:
    print(f"Ocorreu um erro durante a extração: {e}")

finally:
  client.close()

--- Verificando dependências ---
Biblioteca 'influxdb_client' encontrada.
Biblioteca 'openpyxl' encontrada.
Biblioteca 'plotly' encontrada.
---------------------------------

Buscando dados de temperatura da Estação V1...
Sucesso! Foram encontrados 28122 registros brutos no total.

--- DEFINIÇÃO DO PERÍODO DE ANÁLISE ---
Dados disponíveis de 2025-08-19 a 2025-09-01.
Digite a data de início (formato AAAA-MM-DD): 2025-08-21
Digite a data de fim (formato AAAA-MM-DD): 2025-08-31

Filtrando dados de 2025-08-21 até 2025-08-31...
Foram encontrados 24096 registros no período selecionado.

--- Sub-rotina: Limpeza de Dados ---
Registros válidos: 24096 | Registros com dados ausentes: 0

--- Sub-rotina: Agregação de Dados (Janelas de 2min) ---

--- ANÁLISE 1.1: ESTABILIDADE (DESVIO PADRÃO) ---

Ranking de Estabilidade (menor desvio padrão médio é melhor):


Desvio Padrão Médio (°C)
bmp280                   0.005782
bmp388                   0.005925
bmp180                   0.006053
bme280                   0.006278
dht11                    0.007587
lm35dz                   0.008507
aht10                    0.013085
dht22                    0.013195
aht25                    0.014086
mcp9808                  0.021543
ds18b20                  0.021606
lm75                     0.067504


--- ANÁLISE 1.2: RUÍDO E OUTLIERS ---



--- ANÁLISE 1.3: DISPONIBILIDADE DE DADOS (CONFIABILIDADE) ---

Taxa de Falha (percentual de dados ausentes por sensor):


Taxa de Falha (%)
temp.aht10                  0.0
temp.aht25                  0.0
temp.bme280                 0.0
temp.bmp180                 0.0
temp.bmp280                 0.0
temp.bmp388                 0.0
temp.dht11                  0.0
temp.dht22                  0.0
temp.ds18b20                0.0
temp.lm35dz                 0.0
temp.lm75                   0.0
temp.mcp9808                0.0

In [ ]:
# --- 0. PRÉ-CONFIGURAÇÕES | INSTALAÇÃO DE DEPENDÊNCIAS ---
import subprocess
import sys
import base64
from pathlib import Path

def instalar_biblioteca(nome_biblioteca):
    """
    Instala ou atualiza uma biblioteca para a versão mais recente usando pip.
    """
    print(f"Verificando/Atualizando '{nome_biblioteca}'...")
    # Adicionamos o argumento --upgrade para garantir a versão mais recente
    subprocess.check_call([sys.executable, "-m", "pip", "install", "--upgrade", "--quiet", nome_biblioteca])

def verificar_bibliotecas():
    """Verifica se as bibliotecas necessárias estão instaladas e as instala/atualiza se necessário."""
    # Adicionamos kaleido para exportar imagens estáticas e weasyprint para gerar PDF
    # Removed 'chromium-browser' and 'chromium-chromedriver' as they are system packages
    bibliotecas = ['influxdb_client', 'openpyxl', 'plotly', 'kaleido', 'weasyprint']
    print("--- Verificando e atualizando dependências ---")
    for biblioteca in bibliotecas:
        try:
            instalar_biblioteca(biblioteca)
            __import__(biblioteca)
            print(f"Biblioteca '{biblioteca}' está pronta.")
        except ImportError:
             print(f"Falha ao instalar ou importar '{biblioteca}'.")
    print("------------------------------------------")

verificar_bibliotecas()

import pandas as pd
import influxdb_client
import plotly.express as px
from weasyprint import HTML


# --- -1. PRÉ-REQUISITOS DE AMBIENTE (INSTALAÇÃO DO CHROMIUM E DEPENDÊNCIAS) ---
# O Kaleido, motor de exportação de imagem do Plotly, requer um navegador e certas bibliotecas do sistema.
# Esta célula instala o Chromium e suas dependências no ambiente do Colab.
print("--- Instalando pré-requisitos do sistema (Chromium e dependências) para exportação de PDF ---")
try:
    # Adicionamos 'sudo -S' e 'input' para lidar com prompts de senha em ambientes não interativos.
    print("Atualizando lista de pacotes...")
    subprocess.run(["sudo", "-S", "apt-get", "update"], check=True, capture_output=True, text=True, input='\n')
    print("Instalando Chromium e dependências...")
    # Incluindo todas as dependências listadas na mensagem de erro.
    subprocess.run([
        "sudo", "-S", "apt-get", "install", "-y",
        "chromium-browser",
        "chromium-chromedriver",
        "libnss3", "libatk-bridge2.0-0", "libcups2", "libxcomposite1",
        "libxdamage1", "libxfixes3", "libxrandr2", "libgbm1",
        "libxkbcommon0", "libpango-1.0-0", "libcairo2", "libasound2"
    ], check=True, capture_output=True, text=True, input='\n')
    print("Chromium e dependências instalados com sucesso.")
except subprocess.CalledProcessError as e:
    print("Falha ao instalar o Chromium e dependências. A exportção para PDF pode não funcionar.")
    print(e.stderr)
print("-------------------------------------------------------------------------")

# --- 1. CONFIGURAÇÕES INICIAIS ---
influx_url = "https://tsdb.feira-de-jogos.dev.br"
influx_token = "Key-API INFLUXDB"
influx_org = "feira"
influx_bucket = "feira"

pd.set_option('display.max_columns', None)
pd.set_option('display.width', 1000)
pd.set_option('display.max_rows', 100)

# --- FUNÇÕES DE PROCESSAMENTO E ANÁLISE (MODIFICADAS PARA RETORNAR RESULTADOS) ---

def solicitar_intervalo_usuario(df_bruto):
    """Solicita ao usuário as datas de início e fim para a análise e filtra o DataFrame."""
    print("\n--- DEFINIÇÃO DO PERÍODO DE ANÁLISE ---")
    if '_time' not in df_bruto.columns or df_bruto.empty:
        return pd.DataFrame(), None, None
    data_inicio_disponivel = df_bruto['_time'].min()
    data_fim_disponivel = df_bruto['_time'].max()
    print(f"Dados disponíveis de {data_inicio_disponivel.strftime('%Y-%m-%d')} a {data_fim_disponivel.strftime('%Y-%m-%d')}.")
    try:
        data_inicio_str = input(f"Digite a data de início (formato AAAA-MM-DD): ")
        data_fim_str = input(f"Digite a data de fim (formato AAAA-MM-DD): ")
        data_inicio = pd.to_datetime(data_inicio_str).tz_localize('UTC')
        data_fim = pd.to_datetime(data_fim_str + " 23:59:59").tz_localize('UTC')
        print(f"\nFiltrando dados de {data_inicio.date()} até {data_fim.date()}...")
        df_filtrado = df_bruto[(df_bruto['_time'] >= data_inicio) & (df_bruto['_time'] <= data_fim)].copy()
        if df_filtrado.empty: print("Nenhum registro encontrado no período selecionado.")
        else: print(f"Foram encontrados {len(df_filtrado)} registros no período selecionado.")
        return df_filtrado, data_inicio_str, data_fim_str
    except (ValueError, TypeError):
        print("Formato de data inválido. Análise abortada.")
        return pd.DataFrame(), None, None

def limpar_dados(df_bruto):
    """Realiza a limpeza do DataFrame bruto, retornando os DFs limpo e de inválidos."""
    print("\n--- Sub-rotina: Limpeza de Dados ---")
    # ... (código da função inalterado)
    df = df_bruto.copy()
    colunas_sensores = [col for col in df.columns if col.startswith('temp.')]
    indices_invalidos = df[colunas_sensores].isnull().any(axis=1)
    df_invalidos = df[indices_invalidos]
    df_limpo = df.dropna(subset=colunas_sensores)
    print(f"Registros válidos: {len(df_limpo)} | Registros com dados ausentes: {len(df_invalidos)}")
    return df_limpo, df_invalidos


def agregar_dados_por_janela(df_para_agregar, janela='2min'):
    """Realiza a agregação dos dados limpos e retorna o DataFrame agregado."""
    print(f"\n--- Sub-rotina: Agregação de Dados (Janelas de {janela}) ---")
    # ... (código da função inalterado)
    df = df_para_agregar.set_index('_time')
    colunas_sensores = [col for col in df.columns if col.startswith('temp.')]
    df_agregado = df[colunas_sensores].resample(janela).agg(['mean', 'std'])
    return df_agregado


def analisar_estabilidade(df_agregado):
    """Analisa e visualiza a estabilidade dos sensores, retornando a tabela e a figura."""
    print("\n--- ANÁLISE 1.1: ESTABILIDADE (DESVIO PADRÃO) ---")
    df_std = df_agregado.xs('std', level=1, axis=1)
    df_std.columns = [col.replace('temp.', '') for col in df_std.columns]
    std_medio = df_std.mean().sort_values()
    df_resultado = std_medio.to_frame(name='Desvio Padrão Médio (°C)')
    print("\nRanking de Estabilidade (menor desvio padrão médio é melhor):")
    display(df_resultado)
    fig = px.bar(std_medio, orientation='h', labels={'value': 'Desvio Padrão Médio (°C)', 'index': 'Sensor'}, title='Ranking de Estabilidade dos Sensores', text_auto='.4f')
    fig.update_layout(showlegend=False, title_x=0.5)
    # fig.show() # Desativado para não poluir a execução final
    return df_resultado, fig

def analisar_outliers(df_agregado):
    """Analisa e visualiza outliers, retornando a figura."""
    print("\n--- ANÁLISE 1.2: RUÍDO E OUTLIERS ---")
    df_media = df_agregado.xs('mean', level=1, axis=1)
    df_media.columns = [col.replace('temp.', '') for col in df_media.columns]
    df_melted = df_media.melt(var_name='Sensor', value_name='Temperatura Média (°C)')
    fig = px.box(df_melted, x='Sensor', y='Temperatura Média (°C)', title='Distribuição das Leituras de Temperatura e Outliers por Sensor')
    fig.update_layout(title_x=0.5)
    # fig.show() # Desativado para não poluir a execução final
    return fig

def analisar_disponibilidade(df_bruto):
    """Analisa e visualiza a disponibilidade de dados, retornando a tabela e a figura."""
    print("\n--- ANÁLISE 1.3: DISPONIBILIDADE DE DADOS (CONFIABILIDADE) ---")
    colunas_sensores = [col for col in df_bruto.columns if col.startswith('temp.')]
    df_sensores = df_bruto[colunas_sensores]
    taxa_falha = (df_sensores.isnull().sum() / len(df_sensores)) * 100 if len(df_sensores) > 0 else 0
    taxa_falha = taxa_falha.sort_values(ascending=False)
    df_resultado = taxa_falha.to_frame(name='Taxa de Falha (%)')
    print("\nTaxa de Falha (percentual de dados ausentes por sensor):")
    display(df_resultado)
    fig = px.bar(taxa_falha, labels={'value': 'Taxa de Falha (%)', 'index': 'Sensor'}, title='Ranking de Confiabilidade (Menor Taxa de Falha é Melhor)', text_auto='.2f')
    fig.update_layout(showlegend=False, title_x=0.5)
    # fig.show() # Desativado para não poluir a execução final
    return df_resultado, fig

# --- NOVAS FUNÇÕES DE GERAÇÃO DE RELATÓRIO ---

def fig_to_base64(fig):
    """Converte uma figura Plotly em uma string base64 para embutir em HTML."""
    img_bytes = fig.to_image(format="png", width=800, height=500, scale=2)
    return base64.b64encode(img_bytes).decode("utf-8")

def gerar_relatorio_dashboard(data_inicio, data_fim, df_estabilidade, fig_estabilidade, df_disponibilidade, fig_disponibilidade, fig_outliers, nome_arquivo="dashboard_analise_sensores.html"):
    """Gera um arquivo HTML autônomo com os resultados da análise."""
    print(f"\n--- Gerando Dashboard HTML: {nome_arquivo} ---")

    # Converte figuras para imagens embutidas
    img_estabilidade = fig_to_base64(fig_estabilidade)
    img_disponibilidade = fig_to_base64(fig_disponibilidade)
    img_outliers = fig_to_base64(fig_outliers)

    # Converte DataFrames para tabelas HTML
    tabela_estabilidade = df_estabilidade.to_html(classes='table', float_format='{:.4f}'.format)
    tabela_disponibilidade = df_disponibilidade.to_html(classes='table', float_format='{:.2f}%'.format)

    html_template = f"""
    <!DOCTYPE html>
    <html lang="pt-br">
    <head>
        <meta charset="UTF-8">
        <meta name="viewport" content="width=device-width, initial-scale=1.0">
        <title>Relatório de Análise Intrínseca de Sensores</title>
        <style>
            body {{ font-family: 'Segoe UI', Tahoma, Geneva, Verdana, sans-serif; margin: 0; padding: 0; background-color: #f4f7f6; color: #333; }}
            .container {{ max-width: 1200px; margin: 20px auto; padding: 20px; background-color: #fff; box-shadow: 0 0 15px rgba(0,0,0,0.1); border-radius: 8px; }}
            header {{ background-color: #005f73; color: white; padding: 20px; text-align: center; border-radius: 8px 8px 0 0; }}
            header h1 {{ margin: 0; font-size: 2.5em; }}
            header p {{ margin: 5px 0 0; font-size: 1.2em; }}
            .section {{ margin-top: 40px; border-top: 3px solid #0a9396; padding-top: 20px; }}
            h2 {{ color: #005f73; font-size: 1.8em; border-bottom: 2px solid #94d2bd; padding-bottom: 10px; }}
            .grid-container {{ display: grid; grid-template-columns: 1fr 2fr; gap: 30px; align-items: start; margin-top: 20px; }}
            @media (max-width: 900px) {{ .grid-container {{ grid-template-columns: 1fr; }} }}
            .table-container {{ max-height: 500px; overflow-y: auto; }}
            .table {{ width: 100%; border-collapse: collapse; }}
            .table th, .table td {{ padding: 12px; border: 1px solid #ddd; text-align: left; }}
            .table th {{ background-color: #e9d8a6; }}
            .table tr:nth-child(even) {{ background-color: #f9f9f9; }}
            img {{ max-width: 100%; height: auto; border-radius: 5px; box-shadow: 0 4px 8px rgba(0,0,0,0.1); }}
        </style>
    </head>
    <body>
        <div class="container">
            <header>
                <h1>Relatório de Análise Intrínseca de Sensores</h1>
                <p>Projeto UHIMWS - Período de Análise: {data_inicio} a {data_fim}</p>
            </header>

            <div class="section">
                <h2>Análise 1.1: Estabilidade (Precisão)</h2>
                <div class="grid-container">
                    <div class="table-container">
                        <h3>Ranking (Menor Desvio Padrão é Melhor)</h3>
                        {tabela_estabilidade}
                    </div>
                    <div>
                        <img src="data:image/png;base64,{img_estabilidade}" alt="Gráfico de Estabilidade dos Sensores">
                    </div>
                </div>
            </div>

            <div class="section">
                <h2>Análise 1.3: Disponibilidade (Confiabilidade)</h2>
                <div class="grid-container">
                    <div class="table-container">
                        <h3>Ranking (Menor Taxa de Falha é Melhor)</h3>
                        {tabela_disponibilidade}
                    </div>
                    <div>
                        <img src="data:image/png;base64,{img_disponibilidade}" alt="Gráfico de Disponibilidade dos Sensores">
                    </div>
                </div>
            </div>

            <div class="section">
                <h2>Análise 1.2: Distribuição de Leituras e Outliers</h2>
                <div style="text-align: center;">
                    <img src="data:image/png;base64,{img_outliers}" alt="Boxplot de Outliers dos Sensores">
                </div>
            </div>
        </div>
    </body>
    </html>
    """
    with open(nome_arquivo, "w", encoding="utf-8") as f:
        f.write(html_template)
    print(f"Dashboard salvo em '{nome_arquivo}'.")
    return nome_arquivo

def exportar_para_pdf(caminho_html, nome_arquivo_pdf="relatorio_analise_sensores.pdf"):
    """Converte o arquivo HTML gerado para PDF."""
    print(f"\n--- Gerando Relatório PDF: {nome_arquivo_pdf} ---")
    try:
        HTML(caminho_html).write_pdf(nome_arquivo_pdf)
        print(f"Relatório PDF salvo em '{nome_arquivo_pdf}'.")
    except Exception as e:
        print(f"Ocorreu um erro ao gerar o PDF: {e}")

# --- BLOCO DE EXECUÇÃO PRINCIPAL ---

# Check if analysis results already exist from a previous run
if 'df_estabilidade' in locals() and 'fig_estabilidade' in locals() and \
   'df_disponibilidade' in locals() and 'fig_disponibilidade' in locals() and \
   'fig_outliers' in locals() and 'data_inicio_str' in locals() and 'data_fim_str' in locals():
    print("\nUtilizando resultados de análise existentes para gerar relatórios.")
    try:
        # Generate reports using existing results
        caminho_html = gerar_relatorio_dashboard(data_inicio_str, data_fim_str, df_estabilidade, fig_estabilidade, df_disponibilidade, fig_disponibilidade, fig_outliers)
        exportar_para_pdf(caminho_html)
    except Exception as e:
        print(f"Ocorreu um erro ao gerar os relatórios com resultados existentes: {e}")

else:
    # Proceed with data loading and analysis if results are not available
    client = influxdb_client.InfluxDBClient(url=influx_url, token=influx_token, org=influx_org)
    query_api = client.query_api()
    flux_query = f'''
    import "strings"
    from(bucket: "{influx_bucket}")
      |> range(start: -45d)
      |> filter(fn: (r) => r["v"] == "1")
      |> filter(fn: (r) => strings.hasPrefix(v: r["_field"], prefix: "temp."))
      |> pivot(rowKey:["_time"], columnKey: ["_field"], valueColumn: "_value")
    '''
    print("\nBuscando dados de temperatura da Estação V1...")
    df_total = pd.DataFrame()
    try:
        df_total = query_api.query_data_frame(query=flux_query, org=influx_org)

        if not df_total.empty:
            print(f"Sucesso! Foram encontrados {len(df_total)} registros brutos no total.")

            df_periodo_analise, data_inicio_str, data_fim_str = solicitar_intervalo_usuario(df_total)

            if not df_periodo_analise.empty:
                df_limpo, df_invalidos = limpar_dados(df_periodo_analise)
                df_agregado = agregar_dados_por_janela(df_limpo, janela='2min')

                # Executa as análises e captura os resultados (tabelas e figuras)
                df_estabilidade, fig_estabilidade = analisar_estabilidade(df_agregado)
                fig_outliers = analisar_outliers(df_agregado)
                df_disponibilidade, fig_disponibilidade = analisar_disponibilidade(df_periodo_analise)

                # Gera os relatórios
                caminho_html = gerar_relatorio_dashboard(data_inicio_str, data_fim_str, df_estabilidade, fig_estabilidade, df_disponibilidade, fig_disponibilidade, fig_outliers)
                exportar_para_pdf(caminho_html)

        else:
            print("Nenhum dado encontrado para os filtros especificados na consulta inicial.")
    except Exception as e:
        print(f"Ocorreu um erro: {e}")
    finally:
      client.close()

--- Verificando e atualizando dependências ---
Verificando/Atualizando 'influxdb_client'...
Biblioteca 'influxdb_client' está pronta.
Verificando/Atualizando 'openpyxl'...
Biblioteca 'openpyxl' está pronta.
Verificando/Atualizando 'plotly'...
Biblioteca 'plotly' está pronta.
Verificando/Atualizando 'kaleido'...
Biblioteca 'kaleido' está pronta.
Verificando/Atualizando 'weasyprint'...
Biblioteca 'weasyprint' está pronta.
------------------------------------------
--- Instalando pré-requisitos do sistema (Chromium e dependências) para exportação de PDF ---
Atualizando lista de pacotes...
Instalando Chromium e dependências...
Chromium e dependências instalados com sucesso.
-------------------------------------------------------------------------

Utilizando resultados de análise existentes para gerar relatórios.

--- Gerando Dashboard HTML: dashboard_analise_sensores.html ---
Ocorreu um erro ao gerar os relatórios com resultados existentes: It seems like you are running a slim version of 